In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import torch.nn.functional as F


#preparing the data : Given a file, the function prepares 2 arrays
"""
feature_set : each element is an array of 50 readings
targets : each element is a label corrisponding to the readings with the same index in feature_set
"""
def getSamplesFromFiles(filesNames=["mHealth_ECGProcessed_subject3.log"],readingsPerSample=50):
    targets  = np.array([])
    feature_set= np.array([])
    for fileName in filesNames:
        df = pd.read_csv(fileName, header=None, delim_whitespace=True)
        for i in range(int(df.shape[0]/readingsPerSample)):
            if df[2][i*readingsPerSample:i*readingsPerSample+readingsPerSample].mean() in range(1,13):
                feature_set=np.append(feature_set,[df[1][i*readingsPerSample:i*readingsPerSample+readingsPerSample]])
                targets=np.append(targets,df[2][i*readingsPerSample:i*readingsPerSample+readingsPerSample].mean()-1)

    feature_set=feature_set.reshape(int(feature_set.shape[0]/readingsPerSample),readingsPerSample)
#     one_hot_labels=one_hot_labels.reshape(int(one_hot_labels.shape[0]/12),12)
    return feature_set, targets

In [2]:
# define the NN architecture
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        # number of hidden nodes in each layer (512)
        hidden_1 = 60
        hidden_2 = 30
        # linear layer (784 -> hidden_1)
        self.fc1 = nn.Linear(100, hidden_1)
        # linear layer (n_hidden -> hidden_2)
        self.fc2 = nn.Linear(hidden_1, hidden_2)
        self.fc3 = nn.Linear(hidden_2, 12)
        # dropout layer (p=0.2)
        # dropout prevents overfitting of data
        self.dropout = nn.Dropout(0.2)

    def forward(self, x):
        # flatten image input
#         x = x.view(-1, 50)
#         print('XXXXXXXXXXXXX',x.shape,'\n',x)
        # add hidden layer, with relu activation function
        x = F.relu(self.fc1(x))
        x = self.dropout(x)
        x = F.relu(self.fc2(x))
        # add dropout layer
        x = self.dropout(x)
        # add hidden layer, with relu activation function
        x = self.fc3(x)        
        return x

# initialize the NN
model = Net()

In [3]:
feature_set,targets=getSamplesFromFiles(["mHealth_ECGProcessed_subject3.log","mHealth_ECGProcessed_subject4.log","mHealth_ECGProcessed_subject7.log","mHealth_ECGProcessed_subject10.log"],100)

In [4]:
feature_set.shape

(1340, 100)

In [5]:
# specify loss function (categorical cross-entropy)
criterion = nn.CrossEntropyLoss()

# specify optimizer (stochastic gradient descent) and learning rate = 0.01
optimizer = torch.optim.SGD(model.parameters(), lr=0.05)

In [6]:
feature_set=torch.from_numpy(feature_set).float()
targets=torch.from_numpy(targets).long()

# number of epochs to train the model
n_epochs = 100000

# initialize tracker for minimum validation loss
valid_loss_min = np.Inf # set initial "min" to infinity

for epoch in range(n_epochs):
    # monitor training loss
    train_loss = 0.0
    valid_loss = 0.0
    
    ###################
    # train the model #
    ###################
    model.train() # prep model for training
  
    # clear the gradients of all optimized variables
    optimizer.zero_grad()
    # forward pass: compute predicted outputs by passing inputs to the model
    output = model(feature_set)
    # calculate the loss
    loss = criterion(output, targets)
#     print('XXXXXXXXXXXXXX',output[0])
    # backward pass: compute gradient of the loss with respect to model parameters
    loss.backward()
    # perform a single optimization step (parameter update)
    optimizer.step()
    
   
    print('Epoch: {} \tTraining Loss: {:.6f} '.format(
        epoch+1, 
        loss.item()
        ))



Epoch: 1 	Training Loss: 2.491819 
Epoch: 2 	Training Loss: 2.491089 
Epoch: 3 	Training Loss: 2.486724 
Epoch: 4 	Training Loss: 2.489339 
Epoch: 5 	Training Loss: 2.488719 
Epoch: 6 	Training Loss: 2.486313 
Epoch: 7 	Training Loss: 2.485860 
Epoch: 8 	Training Loss: 2.485976 
Epoch: 9 	Training Loss: 2.487386 
Epoch: 10 	Training Loss: 2.484590 
Epoch: 11 	Training Loss: 2.483780 
Epoch: 12 	Training Loss: 2.485652 
Epoch: 13 	Training Loss: 2.480904 
Epoch: 14 	Training Loss: 2.485189 
Epoch: 15 	Training Loss: 2.482879 
Epoch: 16 	Training Loss: 2.481035 
Epoch: 17 	Training Loss: 2.479321 
Epoch: 18 	Training Loss: 2.480330 
Epoch: 19 	Training Loss: 2.479651 
Epoch: 20 	Training Loss: 2.479033 
Epoch: 21 	Training Loss: 2.481293 
Epoch: 22 	Training Loss: 2.482296 
Epoch: 23 	Training Loss: 2.474383 
Epoch: 24 	Training Loss: 2.476523 
Epoch: 25 	Training Loss: 2.478947 
Epoch: 26 	Training Loss: 2.477170 
Epoch: 27 	Training Loss: 2.476024 
Epoch: 28 	Training Loss: 2.475398 
E

Epoch: 248 	Training Loss: 2.433875 
Epoch: 249 	Training Loss: 2.434185 
Epoch: 250 	Training Loss: 2.434060 
Epoch: 251 	Training Loss: 2.430929 
Epoch: 252 	Training Loss: 2.430885 
Epoch: 253 	Training Loss: 2.429056 
Epoch: 254 	Training Loss: 2.433207 
Epoch: 255 	Training Loss: 2.430283 
Epoch: 256 	Training Loss: 2.432331 
Epoch: 257 	Training Loss: 2.427421 
Epoch: 258 	Training Loss: 2.436905 
Epoch: 259 	Training Loss: 2.433012 
Epoch: 260 	Training Loss: 2.430527 
Epoch: 261 	Training Loss: 2.436698 
Epoch: 262 	Training Loss: 2.433916 
Epoch: 263 	Training Loss: 2.435005 
Epoch: 264 	Training Loss: 2.437930 
Epoch: 265 	Training Loss: 2.426292 
Epoch: 266 	Training Loss: 2.431779 
Epoch: 267 	Training Loss: 2.432640 
Epoch: 268 	Training Loss: 2.431422 
Epoch: 269 	Training Loss: 2.429188 
Epoch: 270 	Training Loss: 2.426413 
Epoch: 271 	Training Loss: 2.433229 
Epoch: 272 	Training Loss: 2.430951 
Epoch: 273 	Training Loss: 2.432270 
Epoch: 274 	Training Loss: 2.432820 
E

Epoch: 505 	Training Loss: 2.397979 
Epoch: 506 	Training Loss: 2.395576 
Epoch: 507 	Training Loss: 2.395637 
Epoch: 508 	Training Loss: 2.391306 
Epoch: 509 	Training Loss: 2.400077 
Epoch: 510 	Training Loss: 2.393224 
Epoch: 511 	Training Loss: 2.395219 
Epoch: 512 	Training Loss: 2.394583 
Epoch: 513 	Training Loss: 2.394128 
Epoch: 514 	Training Loss: 2.391383 
Epoch: 515 	Training Loss: 2.393740 
Epoch: 516 	Training Loss: 2.390840 
Epoch: 517 	Training Loss: 2.393615 
Epoch: 518 	Training Loss: 2.390836 
Epoch: 519 	Training Loss: 2.384238 
Epoch: 520 	Training Loss: 2.391467 
Epoch: 521 	Training Loss: 2.391277 
Epoch: 522 	Training Loss: 2.386496 
Epoch: 523 	Training Loss: 2.392544 
Epoch: 524 	Training Loss: 2.389220 
Epoch: 525 	Training Loss: 2.391763 
Epoch: 526 	Training Loss: 2.388007 
Epoch: 527 	Training Loss: 2.387016 
Epoch: 528 	Training Loss: 2.393785 
Epoch: 529 	Training Loss: 2.386433 
Epoch: 530 	Training Loss: 2.389424 
Epoch: 531 	Training Loss: 2.391988 
E

Epoch: 760 	Training Loss: 2.330061 
Epoch: 761 	Training Loss: 2.321236 
Epoch: 762 	Training Loss: 2.331560 
Epoch: 763 	Training Loss: 2.342583 
Epoch: 764 	Training Loss: 2.326031 
Epoch: 765 	Training Loss: 2.329974 
Epoch: 766 	Training Loss: 2.329232 
Epoch: 767 	Training Loss: 2.322332 
Epoch: 768 	Training Loss: 2.327265 
Epoch: 769 	Training Loss: 2.320670 
Epoch: 770 	Training Loss: 2.337579 
Epoch: 771 	Training Loss: 2.328632 
Epoch: 772 	Training Loss: 2.332559 
Epoch: 773 	Training Loss: 2.328470 
Epoch: 774 	Training Loss: 2.329549 
Epoch: 775 	Training Loss: 2.325697 
Epoch: 776 	Training Loss: 2.324474 
Epoch: 777 	Training Loss: 2.333081 
Epoch: 778 	Training Loss: 2.318978 
Epoch: 779 	Training Loss: 2.325415 
Epoch: 780 	Training Loss: 2.322394 
Epoch: 781 	Training Loss: 2.326118 
Epoch: 782 	Training Loss: 2.320363 
Epoch: 783 	Training Loss: 2.324441 
Epoch: 784 	Training Loss: 2.322494 
Epoch: 785 	Training Loss: 2.312372 
Epoch: 786 	Training Loss: 2.325503 
E

Epoch: 1022 	Training Loss: 2.263960 
Epoch: 1023 	Training Loss: 2.252563 
Epoch: 1024 	Training Loss: 2.248916 
Epoch: 1025 	Training Loss: 2.253110 
Epoch: 1026 	Training Loss: 2.252167 
Epoch: 1027 	Training Loss: 2.251005 
Epoch: 1028 	Training Loss: 2.251397 
Epoch: 1029 	Training Loss: 2.256504 
Epoch: 1030 	Training Loss: 2.247207 
Epoch: 1031 	Training Loss: 2.249912 
Epoch: 1032 	Training Loss: 2.252246 
Epoch: 1033 	Training Loss: 2.251959 
Epoch: 1034 	Training Loss: 2.247917 
Epoch: 1035 	Training Loss: 2.247836 
Epoch: 1036 	Training Loss: 2.250473 
Epoch: 1037 	Training Loss: 2.250260 
Epoch: 1038 	Training Loss: 2.243130 
Epoch: 1039 	Training Loss: 2.238927 
Epoch: 1040 	Training Loss: 2.247453 
Epoch: 1041 	Training Loss: 2.252078 
Epoch: 1042 	Training Loss: 2.242189 
Epoch: 1043 	Training Loss: 2.253466 
Epoch: 1044 	Training Loss: 2.239900 
Epoch: 1045 	Training Loss: 2.253028 
Epoch: 1046 	Training Loss: 2.243184 
Epoch: 1047 	Training Loss: 2.248428 
Epoch: 1048 

...

Epoch: 98739 	Training Loss: 0.143969 
Epoch: 98740 	Training Loss: 0.123671 
Epoch: 98741 	Training Loss: 0.143914 
Epoch: 98742 	Training Loss: 0.142046 
Epoch: 98743 	Training Loss: 0.108827 
Epoch: 98744 	Training Loss: 0.142944 
Epoch: 98745 	Training Loss: 0.129606 
Epoch: 98746 	Training Loss: 0.143649 
Epoch: 98747 	Training Loss: 0.130335 
Epoch: 98748 	Training Loss: 0.133858 
Epoch: 98749 	Training Loss: 0.138077 
Epoch: 98750 	Training Loss: 0.125864 
Epoch: 98751 	Training Loss: 0.129621 
Epoch: 98752 	Training Loss: 0.110963 
Epoch: 98753 	Training Loss: 0.131302 
Epoch: 98754 	Training Loss: 0.133170 
Epoch: 98755 	Training Loss: 0.153889 
Epoch: 98756 	Training Loss: 0.152944 
Epoch: 98757 	Training Loss: 0.149142 
Epoch: 98758 	Training Loss: 0.120293 
Epoch: 98759 	Training Loss: 0.135134 
Epoch: 98760 	Training Loss: 0.133394 
Epoch: 98761 	Training Loss: 0.133168 
Epoch: 98762 	Training Loss: 0.137125 
Epoch: 98763 	Training Loss: 0.128892 
Epoch: 98764 	Training Lo

Epoch: 99003 	Training Loss: 0.149872 
Epoch: 99004 	Training Loss: 0.133034 
Epoch: 99005 	Training Loss: 0.162085 
Epoch: 99006 	Training Loss: 0.155001 
Epoch: 99007 	Training Loss: 0.141386 
Epoch: 99008 	Training Loss: 0.113693 
Epoch: 99009 	Training Loss: 0.116247 
Epoch: 99010 	Training Loss: 0.128710 
Epoch: 99011 	Training Loss: 0.134053 
Epoch: 99012 	Training Loss: 0.126033 
Epoch: 99013 	Training Loss: 0.135623 
Epoch: 99014 	Training Loss: 0.140228 
Epoch: 99015 	Training Loss: 0.133752 
Epoch: 99016 	Training Loss: 0.120925 
Epoch: 99017 	Training Loss: 0.142157 
Epoch: 99018 	Training Loss: 0.111060 
Epoch: 99019 	Training Loss: 0.149631 
Epoch: 99020 	Training Loss: 0.145337 
Epoch: 99021 	Training Loss: 0.140580 
Epoch: 99022 	Training Loss: 0.134511 
Epoch: 99023 	Training Loss: 0.110572 
Epoch: 99024 	Training Loss: 0.113104 
Epoch: 99025 	Training Loss: 0.141478 
Epoch: 99026 	Training Loss: 0.114728 
Epoch: 99027 	Training Loss: 0.143034 
Epoch: 99028 	Training Lo

Epoch: 99269 	Training Loss: 0.114054 
Epoch: 99270 	Training Loss: 0.144954 
Epoch: 99271 	Training Loss: 0.117243 
Epoch: 99272 	Training Loss: 0.148569 
Epoch: 99273 	Training Loss: 0.141464 
Epoch: 99274 	Training Loss: 0.145789 
Epoch: 99275 	Training Loss: 0.120077 
Epoch: 99276 	Training Loss: 0.132556 
Epoch: 99277 	Training Loss: 0.136380 
Epoch: 99278 	Training Loss: 0.117003 
Epoch: 99279 	Training Loss: 0.134334 
Epoch: 99280 	Training Loss: 0.129329 
Epoch: 99281 	Training Loss: 0.136387 
Epoch: 99282 	Training Loss: 0.114457 
Epoch: 99283 	Training Loss: 0.138788 
Epoch: 99284 	Training Loss: 0.129248 
Epoch: 99285 	Training Loss: 0.145285 
Epoch: 99286 	Training Loss: 0.112431 
Epoch: 99287 	Training Loss: 0.140788 
Epoch: 99288 	Training Loss: 0.144707 
Epoch: 99289 	Training Loss: 0.126503 
Epoch: 99290 	Training Loss: 0.134432 
Epoch: 99291 	Training Loss: 0.141946 
Epoch: 99292 	Training Loss: 0.123827 
Epoch: 99293 	Training Loss: 0.133410 
Epoch: 99294 	Training Lo

Epoch: 99536 	Training Loss: 0.123080 
Epoch: 99537 	Training Loss: 0.118636 
Epoch: 99538 	Training Loss: 0.160104 
Epoch: 99539 	Training Loss: 0.135986 
Epoch: 99540 	Training Loss: 0.134739 
Epoch: 99541 	Training Loss: 0.137064 
Epoch: 99542 	Training Loss: 0.119889 
Epoch: 99543 	Training Loss: 0.116818 
Epoch: 99544 	Training Loss: 0.122272 
Epoch: 99545 	Training Loss: 0.119040 
Epoch: 99546 	Training Loss: 0.117232 
Epoch: 99547 	Training Loss: 0.140761 
Epoch: 99548 	Training Loss: 0.142501 
Epoch: 99549 	Training Loss: 0.128866 
Epoch: 99550 	Training Loss: 0.114112 
Epoch: 99551 	Training Loss: 0.134715 
Epoch: 99552 	Training Loss: 0.107543 
Epoch: 99553 	Training Loss: 0.163655 
Epoch: 99554 	Training Loss: 0.129846 
Epoch: 99555 	Training Loss: 0.133552 
Epoch: 99556 	Training Loss: 0.126307 
Epoch: 99557 	Training Loss: 0.118455 
Epoch: 99558 	Training Loss: 0.088717 
Epoch: 99559 	Training Loss: 0.137648 
Epoch: 99560 	Training Loss: 0.135491 
Epoch: 99561 	Training Lo

Epoch: 99798 	Training Loss: 0.133956 
Epoch: 99799 	Training Loss: 0.118843 
Epoch: 99800 	Training Loss: 0.128083 
Epoch: 99801 	Training Loss: 0.127460 
Epoch: 99802 	Training Loss: 0.122107 
Epoch: 99803 	Training Loss: 0.152558 
Epoch: 99804 	Training Loss: 0.145718 
Epoch: 99805 	Training Loss: 0.126072 
Epoch: 99806 	Training Loss: 0.151177 
Epoch: 99807 	Training Loss: 0.145134 
Epoch: 99808 	Training Loss: 0.148805 
Epoch: 99809 	Training Loss: 0.132467 
Epoch: 99810 	Training Loss: 0.123780 
Epoch: 99811 	Training Loss: 0.122757 
Epoch: 99812 	Training Loss: 0.142441 
Epoch: 99813 	Training Loss: 0.144427 
Epoch: 99814 	Training Loss: 0.129826 
Epoch: 99815 	Training Loss: 0.135192 
Epoch: 99816 	Training Loss: 0.128282 
Epoch: 99817 	Training Loss: 0.137312 
Epoch: 99818 	Training Loss: 0.113610 
Epoch: 99819 	Training Loss: 0.125376 
Epoch: 99820 	Training Loss: 0.135436 
Epoch: 99821 	Training Loss: 0.111313 
Epoch: 99822 	Training Loss: 0.122683 
Epoch: 99823 	Training Lo

In [7]:
o=450
int((output[o] == output[o].max()).nonzero()[0][0])

2

In [9]:
targets[o]

tensor(2)

In [13]:
def accuracy(out, target):
    t = 0
    for o in range(len(out)):
        if int((output[o] == output[o].max()).nonzero()[0][0]) == int(target[o]):
            t+=1
        print(target[o])
    print(100*t/len(out))
        

In [14]:
accuracy(output,targets)

tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(0)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(1)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(2)
tensor(3)
tensor(3)
tensor(3)
tensor(3)
tensor(3)
tensor(3)
tensor(3)
tensor(3)
tensor(3)
tensor(3)


In [ ]:
# initialize lists to monitor test loss and accuracy
test_loss = 0.0
class_correct = list(0. for i in range(10))
class_total = list(0. for i in range(10))

model.eval() # prep model for evaluation

for data, target in test_loader:
    # forward pass: compute predicted outputs by passing inputs to the model 
    output = model(data)
    # calculate the loss
    loss = criterion(output, target)
    # update test loss 
    test_loss += loss.item()*data.size(0)
    # convert output probabilities to predicted class
    _, pred = torch.max(output, 1)
    # compare predictions to true label
    correct = np.squeeze(pred.eq(target.data.view_as(pred)))
    # calculate test accuracy for each object class
    for i in range(len(target)):
        label = target.data[i]
        class_correct[label] += correct[i].item()
        class_total[label] += 1

# calculate and print avg test loss
test_loss = test_loss/len(test_loader.dataset)
print('Test Loss: {:.6f}\n'.format(test_loss))

for i in range(10):
    if class_total[i] > 0:
        print('Test Accuracy of %5s: %2d%% (%2d/%2d)' % (
            str(i), 100 * class_correct[i] / class_total[i],
            np.sum(class_correct[i]), np.sum(class_total[i])))
    else:
        print('Test Accuracy of %5s: N/A (no training examples)' % (classes[i]))

print('\nTest Accuracy (Overall): %2d%% (%2d/%2d)' % (
    100. * np.sum(class_correct) / np.sum(class_total),
    np.sum(class_correct), np.sum(class_total)))